In [1]:
# Bibliotecas base para análise de dados
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

# Bibliotecas RDKit para química computacional
from rdkit import Chem, DataStructs
from rdkit.Chem import AllChem, PandasTools, Draw, Descriptors, MACCSkeys
from rdkit.Chem import rdFingerprintGenerator
from rdkit.ML.Descriptors import MoleculeDescriptors
from rdkit.Chem.MolStandardize import rdMolStandardize

In [2]:
import pandas as pd

In [3]:
from pandas import DataFrame


class Limpeza:
    """
    Classe para pré-processamento e limpeza de dados moleculares.
    
    Esta classe implementa métodos para sanitização, canonização e
    limpeza de dados de toxicidade molecular, incluindo remoção de
    duplicatas e validação de estruturas SMILES.
    """

    def __init__(self, dataframe: pd.DataFrame) -> None:
        """
        Inicializa a classe Limpeza.
        
        Args:
            dataframe (pd.DataFrame): DataFrame contendo estruturas SMILES
        """
        self.dataframe = dataframe.copy()

    def dados_limpos(
        self,
        col_smiles: str,
        col_valor: str,
        sanitize: bool = True,
        fragmento: bool = False,
        cutoff: float = 0.05,
    ) -> pd.DataFrame:
        """
        Executa o pipeline completo de limpeza e pré-processamento dos dados.
        
        Args:
            col_smiles (str): Nome da coluna contendo estruturas SMILES
            col_valor (str): Nome da coluna contendo valores de toxicidade
            sanitize (bool): Se True, sanitiza as moléculas (padrão: True)
            fragmento (bool): Se True, extrai fragmento principal (padrão: False)
            cutoff (float): Threshold para variação de dados duplicados (padrão: 0.05)
            
        Returns:
            pd.DataFrame: DataFrame limpo e processado
        """
        # Canonização das estruturas SMILES
        df: DataFrame = self.canonical_smiles(
            col_smiles=col_smiles, sanitize=sanitize
        )

        # Remoção de valores nulos e reset do índice
        df.dropna(axis=0, inplace=True)
        df.reset_index(drop=True, inplace=True)

        if fragmento:
            df = self.fragmento_principal(col_smiles=col_smiles)
            df.dropna(axis=0, inplace=True)
            df.reset_index(drop=True, inplace=True)

        df = self.limpa_repetidos(
            col_smiles=col_smiles, col_valor=col_valor, cutoff=cutoff
        )
        df.reset_index(drop=True, inplace=True)

        return df
    
    def canonical_smiles(
        self, col_smiles: str, sanitize: bool = True
    ) -> pd.DataFrame:
        """
        Canoniza estruturas SMILES e aplica sanitização molecular.
        
        Args:
            col_smiles (str): Nome da coluna contendo estruturas SMILES
            sanitize (bool): Se True, aplica sanitização molecular (padrão: True)
            
        Returns:
            pd.DataFrame: DataFrame com SMILES canonizados
        """
        canonical_smiles = []
        valid_indices = []
        
        for index in self.dataframe.index:
            try:
                mol = Chem.MolFromSmiles(
                    self.dataframe[col_smiles].iloc[index]
                )
                
                if sanitize:
                    try:
                        Chem.SanitizeMol(mol)
                        mol_sanitize = rdMolStandardize.Cleanup(mol)
                        
                        uncharger = rdMolStandardize.Uncharger()
                        mol_sanitize = uncharger.uncharge(mol_sanitize)
                        
                        tautomer = rdMolStandardize.TautomerEnumerator()
                        tautomero = tautomer.Canonicalize(mol_sanitize)
                        
                        smile = Chem.MolToSmiles(
                            tautomero, isomericSmiles=False
                        )
                    except Exception:
                        smile = np.nan
                else:
                    smile = Chem.MolToSmiles(mol, isomericSmiles=False)
            except Exception:
                smile = np.nan
            
            canonical_smiles.append(smile)
            
            if smile is not np.nan:
                valid_indices.append(index)
    
        self.dataframe['smiles'] = canonical_smiles
        
        if col_smiles != 'smiles':
            self.dataframe.drop([col_smiles], axis=1, inplace=True)
        
        if sanitize:
            self.dataframe = self.dataframe.loc[valid_indices].reset_index(
                drop=True
            )
    
        return self.dataframe

    def fragmento_principal(self, col_smiles: str) -> pd.DataFrame:
        """
        Extrai o fragmento principal (parent) das estruturas moleculares.
        
        Ideal para análises de clusterização generalistas, removendo
        grupos funcionais específicos e mantendo apenas o esqueleto
        molecular principal.
        
        Args:
            col_smiles (str): Nome da coluna contendo SMILES canonizados
            
        Returns:
            pd.DataFrame: DataFrame com fragmentos principais
        """
        fragmentos = []

        for index in self.dataframe.index:
            try:
                mol = Chem.MolFromSmiles(
                    self.dataframe[col_smiles].iloc[index]
                )
                fragment_parent = rdMolStandardize.FragmentParent(mol)
                fragmento = Chem.MolToSmiles(
                    fragment_parent, isomericSmiles=False
                )
            except Exception:
                fragmento = np.nan
            
            fragmentos.append(fragmento)
            
        self.dataframe['smiles'] = fragmentos
        
        return self.dataframe

    def smiles_repetidos(self, col_smiles: str) -> pd.Series:
        """
        Identifica registros com SMILES duplicados.
        
        Método auxiliar para análise de duplicatas. Utilizado
        internamente pela função limpa_repetidos().
        
        Args:
            col_smiles (str): Nome da coluna contendo SMILES canonizados
            
        Returns:
            pd.Series: Série com SMILES duplicados ordenados
        """
        smiles_duplicados = self.dataframe['smiles'][
            self.dataframe[col_smiles].duplicated()
        ]
    
        return smiles_duplicados.sort_values()
    
    def eda_repetidos(
        self, col_smiles: str, duplicados: pd.Series, col_valor: str
    ) -> pd.DataFrame:
        """
        Realiza análise exploratória de dados (EDA) para registros duplicados.
        
        Método auxiliar que calcula estatísticas descritivas e coeficiente
        de variação para registros com SMILES duplicados.
        
        Args:
            col_smiles (str): Nome da coluna contendo SMILES canonizados
            duplicados (pd.Series): Série com SMILES duplicados
            col_valor (str): Nome da coluna com valores de toxicidade
            
        Returns:
            pd.DataFrame: DataFrame com estatísticas descritivas e CV
        """
        dicio = {}
    
        for duplicado in duplicados:
            eda = self.dataframe[col_valor][
                self.dataframe[col_smiles] == duplicado
            ].describe()
            dicio.update({duplicado: eda})
    
        dataframe_ = pd.DataFrame(data=dicio).T

        # Calcula o coeficiente de variação
        dataframe_['var_coef'] = (dataframe_['std'] / dataframe_['mean'])
    
        return dataframe_
    
    def limpa_repetidos(
        self, col_smiles: str, col_valor: str, cutoff: float = 0.05
    ) -> pd.DataFrame:
        """
        Remove registros duplicados com alta variabilidade.
        
        Remove registros duplicados cujo coeficiente de variação
        excede o threshold especificado, mantendo apenas aqueles
        com baixa variabilidade (representados pela média).
        
        Args:
            col_smiles (str): Nome da coluna contendo SMILES canonizados
            col_valor (str): Nome da coluna com valores de toxicidade
            cutoff (float): Threshold para coeficiente de variação (padrão: 0.05)
            
        Returns:
            pd.DataFrame: DataFrame com duplicatas removidas
        """
        # Identifica registros duplicados
        duplicados = self.smiles_repetidos(col_smiles=col_smiles)
        
        # Calcula estatísticas para registros duplicados
        eda = self.eda_repetidos(
            col_smiles=col_smiles,
            duplicados=duplicados,
            col_valor=col_valor
        )
        
        # Define SMILES com baixa variabilidade para manter
        manter = eda[eda['var_coef'] <= cutoff].index
        
        # Remove registros com alta variabilidade
        dataframe_ = self.dataframe[
            ~self.dataframe[col_smiles].isin(manter)
        ]
    
        # Retorna média dos registros com baixa variabilidade
        return dataframe_.groupby(col_smiles, as_index=False).mean()

In [4]:
# Configuração de arquivos e colunas
# Verifique se os nomes correspondem exatamente aos do seu arquivo
NOME_DO_ARQUIVO_CSV = 'mouse_vi.csv'
NOME_DA_COLUNA_SMILES = 'smiles'
NOME_DA_COLUNA_LD50 = 'mouse_vi' 

# Carregamento e processamento dos dados
try:
    df_bruto = pd.read_csv(NOME_DO_ARQUIVO_CSV)
    print(f"Arquivo '{NOME_DO_ARQUIVO_CSV}' carregado com sucesso.")
    print(f"Número de registros no arquivo original: {len(df_bruto)}\\n")

    # Instanciação e execução da classe de limpeza
    limpador = Limpeza(dataframe=df_bruto)
    
    print("Iniciando processo de limpeza e sanitização...")
    df_limpo = limpador.dados_limpos(
        col_smiles=NOME_DA_COLUNA_SMILES,
        col_valor=NOME_DA_COLUNA_LD50,
        sanitize=True,
        fragmento=False,
        cutoff=0.05
    )
    print("Processo de limpeza finalizado.")
    print(f"Número de registros após a limpeza: {len(df_limpo)}\\n")

    # Exibição dos resultados para verificação
    print("--- Amostra do DataFrame Limpo (Primeiras 5 linhas) ---")
    display(df_limpo.head())

except FileNotFoundError:
    print(f"ERRO: O arquivo '{NOME_DO_ARQUIVO_CSV}' não foi encontrado.")
    print("Verifique se o arquivo está na mesma pasta que este notebook.")
except KeyError as e:
    print(f"ERRO: Coluna não encontrada no arquivo: {e}")
    print("Verifique se os nomes das colunas estão corretos.")

Arquivo 'mouse_vi.csv' carregado com sucesso.
Número de registros no arquivo original: 20441\n
Iniciando processo de limpeza e sanitização...


[19:25:02] Initializing MetalDisconnector
[19:25:02] Running MetalDisconnector
[19:25:02] Initializing Normalizer
[19:25:02] Running Normalizer
[19:25:02] Running Uncharger
[19:25:02] Initializing MetalDisconnector
[19:25:02] Running MetalDisconnector
[19:25:02] Initializing Normalizer
[19:25:02] Running Normalizer
[19:25:02] Running Uncharger
[19:25:02] Initializing MetalDisconnector
[19:25:02] Running MetalDisconnector
[19:25:02] Initializing Normalizer
[19:25:02] Running Normalizer
[19:25:02] Running Uncharger
[19:25:02] Initializing MetalDisconnector
[19:25:02] Running MetalDisconnector
[19:25:02] Initializing Normalizer
[19:25:02] Running Normalizer
[19:25:02] Running Uncharger
[19:25:02] Initializing MetalDisconnector
[19:25:02] Running MetalDisconnector
[19:25:02] Initializing Normalizer
[19:25:02] Running Normalizer
[19:25:02] Running Uncharger
[19:25:02] Initializing MetalDisconnector
[19:25:02] Running MetalDisconnector
[19:25:02] Initializing Normalizer
[19:25:02] Running No

Processo de limpeza finalizado.
Número de registros após a limpeza: 20100\n
--- Amostra do DataFrame Limpo (Primeiras 5 linhas) ---


smiles         cid  mouse_vi
0  Br.Br.Br.COc1ccc2[nH]cc(CCN=C(O)C(N)CSSCC(N)C(...  24843741.0      44.0
1   Br.Br.Br.O=c1[nH]c(NCCSCc2ncccc2Br)ncc1Cc1ccccn1   3048909.0      54.0
2   Br.Br.Br.O=c1[nH]c(NCCSCc2ncccc2Br)ncc1Cc1cccnc1   3048913.0      38.0
3   Br.Br.Br.O=c1[nH]c(NCCSCc2ncccc2Br)ncc1Cc1ccncc1   3078850.0     162.0
4                Br.Br.Br.c1cc(N2CCNCC2)c2[nH]cnc2c1   3069489.0     125.0

In [5]:
def criar_categorias_ghs_oral(df: pd.DataFrame, col_ld50: str) -> pd.DataFrame:
    """
    Cria categorias GHS baseadas nos valores de LD50 oral.
    
    Classifica compostos em categorias de toxicidade GHS (Globally
    Harmonized System) baseado nos valores de LD50 oral em mg/kg.
    
    Args:
        df (pd.DataFrame): DataFrame com dados de toxicidade
        col_ld50 (str): Nome da coluna contendo valores de LD50
        
    Returns:
        pd.DataFrame: DataFrame com categorias GHS adicionadas
    """
    df_copia = df.copy()
    
    # Definição das condições para categorias GHS
    condicoes = [
        df_copia[col_ld50] <= 5,      # Categoria 1: Extremamente tóxico
        (df_copia[col_ld50] > 5) & (df_copia[col_ld50] <= 50),      # Categoria 2: Muito tóxico
        (df_copia[col_ld50] > 50) & (df_copia[col_ld50] <= 300),    # Categoria 3: Tóxico
        (df_copia[col_ld50] > 300) & (df_copia[col_ld50] <= 2000),  # Categoria 4: Nocivo
        (df_copia[col_ld50] > 2000) & (df_copia[col_ld50] <= 5000)  # Categoria 5: Pode ser nocivo
    ]
    
    categorias = [1, 2, 3, 4, 5]
    df_copia['GHS_Category'] = np.select(
        condicoes, categorias, default=np.nan
    )
    
    # Remove registros que não se enquadram nas categorias
    df_copia.dropna(subset=['GHS_Category'], inplace=True)
    df_copia['GHS_Category'] = df_copia['GHS_Category'].astype(int)
    
    return df_copia

In [7]:
import os

try: 
    nome_base, extensao = os.path.splitext(NOME_DO_ARQUIVO_CSV)
    
    # Nome da coluna que contém o LD50
    coluna_ld50 = nome_base

    # Arquivo de saída
    arquivo_saida = f"{nome_base}_classificado{extensao}"

    print("--- Iniciando o mapeamento de categoria GHS ---")
    print(f"Usando a coluna '{coluna_ld50}' para os valores de LD50")

    # Aplicação da função de mapeamento
    df_mapeado = criar_categorias_ghs_oral(
        df=df_limpo,
        col_ld50=coluna_ld50
    )

    print("\\n--- Resumo da Distribuição de Categorias ---")
    print(df_mapeado['GHS_Category'].value_counts().sort_index())
    print("\\n" + "="*50 + "\\n")

    # Salvamento do arquivo processado
    df_mapeado.to_csv(arquivo_saida, index=False)

    print(f"DataFrame mapeado e salvo com sucesso como: '{arquivo_saida}'")

except NameError as e:
    print(f"ERRO: Variável não definida: {e}")
    print("Certifique-se de que 'df_limpo' e 'NOME_DO_ARQUIVO_CSV' foram definidos nas células anteriores")
except KeyError as e:
    print(f"ERRO: Coluna não encontrada: {e}")
    print(f"Verifique se o arquivo '{NOME_DO_ARQUIVO_CSV}' contém uma coluna chamada '{coluna_ld50}'.")


--- Iniciando o mapeamento de categoria GHS ---
Usando a coluna 'mouse_vi' para os valores de LD50
\n--- Resumo da Distribuição de Categorias ---
1    1106
2    7214
3    9246
4    1976
5     309
Name: GHS_Category, dtype: int64
\n==================================================\n
DataFrame mapeado e salvo com sucesso como: 'mouse_vi_classificado.csv'
